#Test

##Setup

In [ ]:
from google.colab import drive
drive.mount("/content/drive/")

Mounted at /content/drive/


In [ ]:
WorkDir = "/content/drive/MyDrive/tensorflow_project/Disease Prediction/data/4.5 - Multilingual USE/"

In [ ]:
import os
os.chdir(WorkDir)

In [ ]:
!pip install llama-index

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.4/15.4 MB 70.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 80.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.3/268.3 kB 30.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 10.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 136.1/136.1 kB 18.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 86.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 290.4/290.4 kB 34.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 10.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 8.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 6.8 MB/s eta 0:00:00


In [ ]:
!pip install pymongo

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 676.9/676.9 kB 12.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 307.7/307.7 kB 34.0 MB/s eta 0:00:00


In [ ]:
!pip install llama-index-llms-ollama

In [ ]:
import time
import json
import requests
import numpy as np
import pandas as pd

from tqdm import tqdm

In [ ]:
from google.colab import userdata
vectara_customer_id = userdata.get('VECTARA_CUSTOMER_ID')
vectara_index_query_api = userdata.get('VECTARA_INDEX_QUERY_API')
vectara_personal_api = userdata.get('VECTARA_PERSONAL_API')
os.environ['OPENAI_API_KEY'] = userdata.get('OPENAI_API_KEY')

##LlamaIndex

In [ ]:
from llama_index.core import VectorStoreIndex, SimpleDirectoryReader

In [ ]:
from llama_index.core import Settings
from llama_index.llms.ollama import Ollama
from llama_index.llms.openai import OpenAI

###Simple Query

In [ ]:
# # Global settings
# Settings.llm = Ollama(model="mistral", request_timeout=60.0)
Settings.llm = OpenAI(model="gpt-3.5-turbo-0125", temperature=0.1)

# # Local settings
# index.as_query_engine(llm=Ollama(model="mistral", request_timeout=60.0))

In [ ]:
documents = SimpleDirectoryReader("./Documents/").load_data()
index = VectorStoreIndex.from_documents(documents)

In [ ]:
query_engine = index.as_query_engine(streaming=True)
response = query_engine.query("Summarize this book")
response.print_response_stream()

The book discusses the challenges patients face in adhering to lifestyle changes compared to medication regimens. It emphasizes the importance of clear communication, culturally appropriate health services, and strategies to improve adherence to long-term regimens. Additionally, it provides recommendations for clinicians on screening for smoking, counseling for tobacco cessation, and prescribing pharmacotherapy. The book also outlines the USPSTF recommendations regarding the provision of specific services to eligible patients.

###FLARE

In [ ]:
index_query_engine = index.as_query_engine(similarity_top_k=2)

In [ ]:
from llama_index.core.query_engine import FLAREInstructQueryEngine

flare_query_engine = FLAREInstructQueryEngine(
    query_engine=index_query_engine,
    max_iterations=7,
    verbose=True,
)

In [ ]:
response = flare_query_engine.query(
    "How the Covid-19 impact the healthcare system and how did we survive and thrive through the pandemic?"
)

Query: How the Covid-19 impact the healthcare system and how did we survive and thrive through the pandemic?
Current response: 
Lookahead response: [Search(How did Covid-19 impact the healthcare system?)]
Updated lookahead response: Covid-19 impacted the healthcare system by revealing and exacerbating profound inequities in health and healthcare. Additionally, Covid-19 resulted in a significant toll on morbidity and mortality, with higher mortality rates observed in certain demographic groups compared to others. The pandemic highlighted the importance of vaccination and preventive measures to protect against Covid-19.
Current response:  Covid-19 impacted the healthcare system by revealing and exacerbating profound inequities in health and healthcare. Additionally, Covid-19 resulted in a significant toll on morbidity and mortality, with higher mortality rates observed in certain demographic groups compared to others. The pandemic highlighted the importance of vaccination and preventive 

###HyDE

In [ ]:
from llama_index.core.indices.query.query_transform import HyDEQueryTransform
from llama_index.core.query_engine import TransformQueryEngine

from IPython.display import Markdown, display

In [ ]:
query_str = "How the Covid-19 impact the healthcare system and how did we survive and thrive through the pandemic?"

Without Transformation

In [ ]:
query_engine = index.as_query_engine()
response = query_engine.query(query_str)
display(Markdown(f"<b>{response}</b>"))

<b>Empty Response</b>

With HyDE

In [ ]:
hyde = HyDEQueryTransform(include_original=True)
hyde_query_engine = TransformQueryEngine(query_engine, hyde)
response = hyde_query_engine.query(query_str)
display(Markdown(f"<b>{response}</b>"))

<b>Empty Response</b>

##MongoDB

###Connection Check

In [ ]:
!pip install llama-index-vector-stores-mongodb

In [ ]:
# Provide URI to constructor, or use environment variable

from llama_index.vector_stores.mongodb import MongoDBAtlasVectorSearch
from llama_index.core import VectorStoreIndex
from llama_index.core import StorageContext
from llama_index.core import SimpleDirectoryReader

import time
import pymongo

In [ ]:
import openai

openai.api_key = userdata.get('OPENAI_API_KEY')

In [ ]:
os.environ['MONGO_URI'] = userdata.get('MONGO_URI')

In [ ]:
# Create a new client and connect to the server
client = pymongo.MongoClient(uri)

# Send a ping to confirm a successful connection
try:
    client.admin.command('ping')
    print("Pinged your deployment. You successfully connected to MongoDB!")
except Exception as e:
    print(e)

# if client:
#     print('success')
# else :
#     print('failed')

Pinged your deployment. You successfully connected to MongoDB!


In [ ]:
# construct store
store = MongoDBAtlasVectorSearch(mongodb_client = client,
                                 db_name = 'DeepSymp',
                                 collection_name = 'medical-textbook',
                                 index_name = 'vector_index')
storage_context = StorageContext.from_defaults(vector_store=store)

In [ ]:
start = time.time()

docs = SimpleDirectoryReader("./Test_Documents/").load_data(num_workers=8)

end = time.time()

print(end - start)

In [ ]:
start = time.time()

# construct index
index = VectorStoreIndex.from_documents(
    docs,
    storage_context=storage_context
)

end = time.time()

print(end - start)

In [ ]:
query_str = "What is Patient Adherence?"

In [ ]:
query_engine = index.as_query_engine()
response = query_engine.query(query_str)
print(response)

Patient adherence refers to the extent to which a patient follows medical advice and treatment recommendations provided by healthcare professionals. This includes taking medications as prescribed, attending appointments, following lifestyle recommendations, and actively participating in their own care. Adherence is crucial for the effectiveness of treatments and overall health outcomes.


In [ ]:
# retrive index
index = VectorStoreIndex.from_vector_store(store)

In [ ]:
query_str = "What is Patient Adherence?"

In [ ]:
query_engine = index.as_query_engine()
response = query_engine.query(query_str)
print(response)

Patient adherence refers to the extent to which a patient follows medical advice and treatment plans as prescribed by healthcare providers. It involves taking medications as directed, attending appointments, following lifestyle recommendations, and actively participating in their own care. Adherence plays a crucial role in the effectiveness of treatments and overall health outcomes.


###Semantic Chunking (llamaIndex)

In [ ]:
!pip install llama-index-embeddings-openai

In [ ]:
from llama_index.core.node_parser import (
    SentenceSplitter,
    SemanticSplitterNodeParser,
)
from llama_index.embeddings.openai import OpenAIEmbedding

import os

In [ ]:
start = time.time()

docs = SimpleDirectoryReader("./Test_Documents/").load_data(num_workers=8)

end = time.time()

print(end - start)

10.19366717338562


In [ ]:
embed_model = OpenAIEmbedding()
splitter = SemanticSplitterNodeParser(
    buffer_size=2, breakpoint_percentile_threshold=95, embed_model=embed_model
)

In [ ]:
nodes = splitter.get_nodes_from_documents(docs, show_progress = True)

Parsing nodes:   0%|          | 0/448 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/1 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/1 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/11 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/1 [00:00<?, ?it/s]

...

Generating embeddings:   0%|          | 0/17 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/17 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/1 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/29 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/12 [00:00<?, ?it/s]

In [ ]:
vector_index = VectorStoreIndex(nodes)
query_engine = vector_index.as_query_engine()

In [ ]:
response = query_engine.query(
    "If patient comes with these symptoms: nasal congestion, facial pain or pressure, postnasal drip, cough, fatigue, headache, and reduced sense of smell. What disease the patient might have, list me 3 possibilities? Why?"
)

In [ ]:
display(Markdown(f"<b>{response}</b>"))

<b>The patient might have sinusitis, allergic rhinitis, or nasal polyps. Sinusitis is a common condition characterized by nasal congestion, facial pain or pressure, postnasal drip, cough, fatigue, headache, and reduced sense of smell. Allergic rhinitis shares similar symptoms but is triggered by allergens. Nasal polyps can also present with these symptoms and are noncancerous growths in the lining of the nasal passages or sinuses.</b>

In [ ]:
from llama_index.core.response.notebook_utils import display_source_node

for n in response.source_nodes:
    display_source_node(n, source_length=20000)

**Node ID:** 8a97888f-e059-4299-92c7-09181d171964<br>**Similarity:** 0.825074351231588<br>**Text:** 158
DIFFERENTIAL DIAGNOSIS IN INTERNAL MEDICINECLINICAL FEATURES
The usual symptoms at presentation are cough, chest pain, fever, chills 
and dyspnea. Localized symptoms are secondary to tumour invasion (res-
piratory compromise; paralysis of the limbs, diaphragm and vocal cords; 
Horner syndrome; superior vena cava syndrome), while systemic symptoms are typically due to the release of excess hormones, antibodies or cytokines.
Superior vena cava syndrome is suspected in a patient with engorge-
ment of veins of the upper part of the body with resultant edema and suf-fusion in the head, face and neck. There may be orthopnea and elevation 
of jugular venous pressure ( JVP). Dyspnea is the most common symptom, 
observed in these patients. Other symptoms include facial swelling, head 
fullness, cough, arm swelling, chest pain, dysphagia, orthopnea, distorted 
vision, hoarseness, stridor, headache, nasal stuffiness, nausea, pleural effu-sions, and light-headedness. The characteristic physical findings of superior 
vena cava syndrome include venous distention of the neck and chest wall, 
facial edema, upper-extremity edema, mental changes, plethora, cyanosis, papilledema, stupor, and even coma. Central nervous system symptoms are 
caused by impeded venous return and resultant cerebral edema; the patient 
may have lethargy, confusion, headache, irritability, blurred vision or syn-cope. Clinically, the important parameters of severity of superior mediasti-
nal syndrome (SMS) include the degree, as well as rapidity of obstruction. 
In patients with non-Hodgkin lymphoma involving the mediastinal nodes, 
there may be rapid enlargement of the nodes in size.<br>

**Node ID:** 65eebd7b-025d-4db6-bf41-1881e7d33b19<br>**Similarity:** 0.824518704925105<br>**Text:** 110
DIFFERENTIAL DIAGNOSIS IN INTERNAL MEDICINEBody pletismography: increased residual volume (RV) and increased 
total lung capacity (TLC) in case of emphysema.
Common causes of bronchial obstruction:
• Bronchial asthma
• Chronic obstructive pulmonary disease (COPD)
• Acute bronchitis
• Left heart failure
• Gastroesophageal reflux disease
• Chronic sinusitis
• Bronchiectasis
• Pulmonary embolism
Less common causes of bronchial obstruction:• Alpha1-antitripsin deficiency
• Aspergillosis
• Cystic fibrosis
• Tuberculosis of bronchi
• Local obstruction by tumor or foreign body aspiration
• Bronchiolitis
• Vocal cord dysfunction
• Sarcoidosis
• Tracheomalacia
• Carcinoid syndrome
• Churg-Strauss syndrome
Bronchial asthma. The symptoms and signs include: increased night-
time cough, cough or wheezing with physical activity, tiredness with activ-ities, restless sleep or waking up tired, worsening allergy symptoms (aller-gic rhinitis, dark circles under eyes or skin allergy). Anamnestic clues for the diagnosis: episodes may be exacerbated by exposure to irritants such as tobacco smoke or fumes from chemicals.<br>

In [ ]:
query_str = "If patient comes with these symptoms: nasal congestion, facial pain or pressure, postnasal drip, cough, fatigue, headache, and reduced sense of smell. What disease the patient might have, list me 3 possibilities? Why?"

In [ ]:
hyde = HyDEQueryTransform(include_original=True)
hyde_query_engine = TransformQueryEngine(query_engine, hyde)
response = hyde_query_engine.query(query_str)
display(Markdown(f"<b>{response}</b>"))

<b>The patient with symptoms of nasal congestion, facial pain or pressure, postnasal drip, cough, fatigue, headache, and reduced sense of smell might have sinusitis, allergic rhinitis, or nasal polyps. Sinusitis is a common condition characterized by inflammation of the sinuses, leading to symptoms such as nasal congestion, facial pain, cough, fatigue, and headache. Allergic rhinitis presents with similar symptoms due to an allergic reaction to allergens like pollen or dust mites. Nasal polyps can cause nasal congestion, postnasal drip, reduced sense of smell, and facial pressure. These conditions are considered because they align with the patient's symptoms related to sinus and nasal issues.</b>

# RAG

##Setup

In [ ]:
from google.colab import drive
drive.mount("/content/drive/")

Mounted at /content/drive/


In [ ]:
WorkDir = "/content/drive/MyDrive/tensorflow_project/Disease Prediction/data/4.5 - Multilingual USE/"

In [ ]:
import os
os.chdir(WorkDir)

Install Library

In [ ]:
!pip install llama-index-vector-stores-mongodb
!pip install llama-index-embeddings-openai
!pip install llama-index
!pip install pymongo

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.4/15.4 MB 53.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 676.9/676.9 kB 44.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 136.0/136.0 kB 12.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.3/268.3 kB 23.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 58.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 307.7/307.7 kB 26.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 7.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 5.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 17.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.9/3.9 MB 24.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━

Import Libray

In [ ]:
import time
import json
import openai
import pymongo
import requests
import numpy as np
import pandas as pd

from tqdm import tqdm
from google.colab import userdata
from IPython.display import Markdown, display

from llama_index.core import Settings
from llama_index.llms.openai import OpenAI
from llama_index.core import StorageContext
from llama_index.embeddings.openai import OpenAIEmbedding
from llama_index.core.query_engine import TransformQueryEngine
from llama_index.core.node_parser import SemanticSplitterNodeParser
from llama_index.core import VectorStoreIndex, SimpleDirectoryReader
from llama_index.vector_stores.mongodb import MongoDBAtlasVectorSearch
from llama_index.core.response.notebook_utils import display_source_node
from llama_index.core.indices.query.query_transform import HyDEQueryTransform

Loading Credentials

In [ ]:
openai.api_key = userdata.get('OPENAI_API_KEY')
os.environ['MONGO_URI'] = userdata.get('MONGO_URI')
os.environ['OPENAI_API_KEY'] = userdata.get('OPENAI_API_KEY')

Set up Global LLM

In [ ]:
Settings.llm = OpenAI(model="gpt-3.5-turbo-0125", temperature=0.1)

##Semantic Chunking

In [ ]:
start = time.time()

docs = SimpleDirectoryReader("./Documents/").load_data(num_workers=8)

end = time.time()

print(end - start)

226.2761800289154


In [ ]:
embed_model = OpenAIEmbedding()
splitter = SemanticSplitterNodeParser(
    buffer_size=2, breakpoint_percentile_threshold=95, embed_model=embed_model
)

In [ ]:
nodes = splitter.get_nodes_from_documents(docs, show_progress = True)

Parsing nodes:   0%|          | 0/6684 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/2 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/3 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/1 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/4 [00:00<?, ?it/s]

...

Generating embeddings:   0%|          | 0/1 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/1 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/1 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/1 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/1 [00:00<?, ?it/s]

##MongoDB Atlas

In [ ]:
uri = userdata.get('MONGO_URI')

In [ ]:
# Create a new client and connect to the server
client = pymongo.MongoClient(uri)

# Send a ping to confirm a successful connection
try:
    client.admin.command('ping')
    print("Pinged your deployment. You successfully connected to MongoDB!")
except Exception as e:
    print(e)

Pinged your deployment. You successfully connected to MongoDB!


In [ ]:
store = MongoDBAtlasVectorSearch(mongodb_client = client,
                                 db_name = 'DeepSymp',
                                 collection_name = 'medical-textbook',
                                 index_name = 'vector_index')
storage_context = StorageContext.from_defaults(vector_store=store)

###First Time

In [ ]:
start = time.time()

# construct index
index = VectorStoreIndex(
    nodes,
    storage_context=storage_context
)

end = time.time()

print(end - start)

476.0685291290283


!!!!!!!! MUST CREATE INDICES IN MONGODB ATLAS !!!!!!!!

```
{
  "fields":[
    {
      "type": "vector",
      "path": "embedding",
      "numDimensions": 1536,
      "similarity": "cosine"
    }
  ]
}
```



###Retrive From Database

In [ ]:
start = time.time()

index = VectorStoreIndex.from_vector_store(store)

end = time.time()

print(end - start)

0.0006113052368164062


##Hypothetical Document Embeddings

In [ ]:
symptoms = " I am red rash around my male genital. I'm not gay and I didn't have sex yet"

In [ ]:
query_str = f"""If a patient presents with the following symptoms:\n
                {symptoms},\n
                please provide three possible diseases and reasons why using bullet points.\n
                Should the patient seek professional medical attention or opt for self-care at a pharmacy?\n
                Additionally, outline the treatment options for each identified diseases"""

Without HyDE

In [ ]:
query_engine = index.as_query_engine(similarity_top_k=10)
response = query_engine.query(query_str)
display(Markdown(f"<b>{response}</b>"))

<b>- Contact dermatitis: Red rash around the male genital area can be caused by contact dermatitis, which is an inflammatory skin reaction triggered by contact with irritants or allergens.
- Folliculitis: Infection around the base of the hairs can lead to redness and rash in the genital area, especially if there is shaving involved.
- Intertrigo: Infected eczema in skin creases can also present as a red rash in the genital region.

The patient should seek professional medical attention to accurately diagnose the underlying cause of the rash and receive appropriate treatment.

Treatment options:
- Contact dermatitis: Topical corticosteroids, antihistamines, and avoiding the irritant.
- Folliculitis: Antibacterial washes, topical antibiotics, and warm compresses.
- Intertrigo: Keeping the area dry, using antifungal creams, and wearing breathable clothing.</b>

With HyDE

In [ ]:
hyde = HyDEQueryTransform(include_original=True)
hyde_query_engine = TransformQueryEngine(query_engine, hyde)
response = hyde_query_engine.query(query_str)
display(Markdown(f"<b>{response}</b>"))

<b>- Balanitis/Balanoposthitis: Inflammation of the glans/prepuce can present with redness, pruritus, and white pustules. It can be caused by various factors such as infections or irritants.
- Candidiasis: A fungal infection that can cause an itchy rash with 'satellite' pustules outside the rash. It is commonly associated with conditions like diabetes mellitus.
- Contact dermatitis: Exposure to potential allergens like chemicals or certain fabrics can lead to redness and itching. Avoiding the triggering substances is crucial for management.

The patient should seek professional medical attention for an accurate diagnosis and appropriate treatment. Self-care at a pharmacy may not address the underlying cause effectively.

Treatment options:
- Balanitis/Balanoposthitis: Treatment may involve antifungal or antibiotic creams, proper hygiene practices, and addressing any underlying infections or irritants.
- Candidiasis: Management includes antifungal medications like clotrimazole or miconazole, along with addressing any underlying conditions like diabetes.
- Contact dermatitis: Avoiding the allergen or irritant is key. Topical steroid creams and emollients can help alleviate symptoms.</b>

In [ ]:
for n in response.source_nodes:
    display_source_node(n, source_length=2000)

**Node ID:** 96c7889f-f31b-4c10-8442-24de6275c53f<br>**Similarity:** 0.9326599836349487<br>**Text:** Common presenting symptoms
These include:
•	 a	rash:	scaly,	blistering	or	itchy
•	 a	lump	or	lesion•	 pruritus 	(itch)
•	 hair	loss	or	excess	hair	(hirsutism, 	hypertrichosis)
•	 nail	changes.
Ask:
•	 When	did	the	lesion	appear	or	the	rash	begin?
•	 Where 	is	the	rash/lesion?
•	 Has	the	rash	spread,	or	the	lesion	changed,	since	its	
onset?
•	 Is	the	lesion	tender	or	painful?	Is	the	rash	itchy?	Is	the	itch	
intense enough to cause bleeding by scratching or to 
disturb	sleep,	as	in	atopic	eczema	and	lichen	simplex?	Are	
there	blisters?
•	 Do	the	symptoms 	vary	with	time?	For	example,	the	
pruritus of scabies is usually worse at night, and acne  
and atopic eczema may show a premenstrual exacerbation.
•	 Were	there	any	preceding 	symptoms, 	such	as	a	 
sore throat in psoriasis, a severe illness in telogen effluvium, or a new oral medication in drug  
eruptions?
•	 Are	there	any	aggravating 	or	relieving	factors?	For	
example, exercise or exposure to heat may precipitate cholinergic urticaria.
•	 What,	if	any,	has	been	the	effect	of	topical	or	oral	
medications? 	Self-medication 	with	oral	antihistamines 	may	
ameliorate urticaria, and topical glucocorticoids may help inflammatory reactions.
•	 Are	there	any	associated 	constitutional 	symptoms, 	 
such as joint pain (psoriasis), muscle pain and  
weakness (dermatomyositis), fever, fatigue or  
weight	loss?
•	 Very	importantly, 	what	is	the	impact	of	the	rash	on	the	
individual’s 	quality	of	life?
Past medical and drug history
Ask about general health and previous medical or skin conditions; a history of asthma, hay fever or childhood eczema suggests atopy. Coeliac disease is associated with dermatitis herpetiformis.
Take a full drug history, including any recent oral or topical 
prescribed or over-the-counter medication. Enquire about allergies not just to medicines but also to animals or foods.
Fig. 14.2
 Structure of the nail.<br>

**Node ID:** f953aeb7-8f0f-4b30-a558-23f5ecec1633<br>**Similarity:** 0.9324778318405151<br>**Text:** Explain	what	you	are	going	to	do	and	why	it	is	necessary, 	
and	offer	a	chaperone. 	Record	the	chaperone’s 	name;	if	the	
offer is refused, record the fact. Apply alcohol gel and put on gloves. Allow the patient privacy to undress.
Ask the patient to stand and expose the area from his lower 
abdomen to the top of his thighs, unless you are examining the 
inguinoscrotal 	area.	In	this	case,	ask	him	to	lie	on	his	back	initially.
Skin
Examination sequence
• Look in turn at the groin, skin creases, perineum and 
scrotal skin for redness, swellings or ulcers. Note the hair 
distribution.
•	 If	you	see	any	swellings	in	the	groin,	palpate	these	and	
define	them	using	‘SPACESPIT’ 	(see	Box	3.8).
There may be alopecia or an infestation. Patients who shave 
their pubic hair may have dermatitis or folliculitis (infection around the base of the hairs), causing an irritating red rash. 
Intertrigo	(infected	eczema)	occurs	in	the	skin	creases,	and	
lymphadenopathy may stem from local or general causes.
Scrotal oedema can be caused by systemic or local disease. 
Heart	and	liver	dysfunction 	may	lead	to	significant	genital	oedema,	
as may nephrotic syndrome and lymphoedema due to pelvic lymphadenopathy.
Penis
Examination sequence
• Look at the shaft and check the position of the urethral 
opening to exclude hypospadias (urethra opening partway 
along the shaft of the penis; see Fig. 15.11A).
• Palpate the shaft for fibrous plaques (usually on the 
dorsum). Palpate any other lesions to define them.
• Retract the prepuce and inspect the glans for red patches 
or vesicles.Consider possible precipitating events: for example, relationship 
difficulties or trauma. Assess cardiovascular, neurological and psychiatric comorbidities as well as taking a drug history.
If	the	patient	has	never	had	an	erection,	he	may	have	primary	
ED	due	to	an	anatomical 	abnormality. 	Secondary 	ED	is	more	
common and may be psychological or organic in aetiology. 
Psychological 	ED	may	have	a	precipitating 	...<br>

**Node ID:** c8350183-09c6-4cbb-8fbc-930b6e032664<br>**Similarity:** 0.9301568865776062<br>**Text:** emollient, antihistamines, 
withdrawal of most recently used drugs, e.g. 
antibiotics.
Viral exanthema from 
unknown agentSuggested by:  red, non-itchy rash with uniform 
pigmentation. Related systemic symptoms.
Confirmed by:  appearance, spontaneous 
resolution.
Finalized by the predictable outcome of  
management, e.g.  antipyretic.
Measles Suggested by:  red, non-itchy rash with uniform 
pigmentation. Related systemic symptoms.
Confirmed by:  appearance, spontaneous 
resolution, consistent with an incubation 
period of 0–4 days. 
Finalized by the predictable outcome of  
management, e.g.  antipyretic.
Rubella (in pregnant 
mothers complicated by 
congential malformation)Suggested by:  red, non-itchy rash with uniform 
pigmentation. Related systemic symptoms.
Confirmed by:  appearance, spontaneous 
resolution, consistent with an incubation 
period of 4–2 days.<br>

**Node ID:** 677961b0-1d8d-4e8d-b84b-61cf5b7e6294<br>**Similarity:** 0.9284493923187256<br>**Text:** Pruritus accompanying serious internal disease may not 
respond to any type of therapy.
Jeon J et al. Treatment of patients with chronic pruritus of 
unknown origin with dupilumab. J Dermatolog Treat. 2022;  
33:1754. [PMID: 33557654]
Kabashima K et al; Nemolizumab-JP01 Study Group. Trial of 
nemolizumab and topical agents for atopic dermatitis with 
pruritus. N Engl J Med. 2020;383:141. [PMID: 32640132]
Misery L et al. Chronic itch: emerging treatments following new 
research concepts. Br J Pharmacol. 2021;178:4775. [PMID: 
34463358]
Satoh T et al. 2020 guidelines for the diagnosis and treatment 
of cutaneous pruritus. J Dermatol. 2021;48:e399. [PMID: 
34288036]
Sutaria N et al. Itch: pathogenesis and treatment. J Am Acad 
Dermatol. 2022;86:17. [PMID: 34648873]
Anogenital Pruritus
ESSENTIALS OF DIAGNOSIS
 »Anogenital itching, chiefly nocturnal.
 »Skin findings are highly variable, ranging from 
none to excoriations and inflammation of any 
degree, including lichenification.
 »General Considerations
Anogenital pruritus may be due to a primary inflammatory 
skin disease (intertrigo, psoriasis, lichen simplex chronicus, 
seborrheic dermatitis, lichen sclerosus), contact dermatitis 
(soaps, wipes, colognes, douches, and topical treatments), 
irritating secretions (diarrhea, leukorrhea, or trichomonia -
sis), infections (candidiasis, dermatophytosis, erythrasma), 
or oxyuriasis (pinworms). Erythrasma is diagnosed by coral-
red fluorescence with Wood light and cured with erythromy -
cin. Squamous cell carcinoma of the anus and extramammary 
Paget disease are rare causes of genital pruritus.
In pruritus ani, hemorrhoids are often found, and leak -
age of mucus and bacteria from the distal rectum onto the 
perianal skin may be important in cases in which no other 
skin abnormality is found.
Many women experience pruritus vulvae. Pruritus vul -
vae does not usually involve the anal area, though anal itch -
ing may spread to the vulva. In men, pruritus of the scrotum 
is ...<br>

**Node ID:** bc7078a9-e5b6-4009-9e8e-deac952d331f<br>**Similarity:** 0.928291916847229<br>**Text:** Page 312 / 394In men: balanitis/balanoposthitis
(inﬂammation of the glans/prepuce,
erythema, pruritus, white pustules)
and rarely urethritispH of vaginal ﬂuid:
normalIn men:
miconazole 2%
cream: 1 application
2 times daily for 7
days
Herpes
simplex
virus type 2
(genital herpes)Many asymptomatic carriers. Multiple
vesicles on genitals leading to painful
ulcerations. In women, affects vulva,
vagina and cervix; in males, penis and
sometimes urethra.<br>

**Node ID:** 923bb485-9445-44b8-b2f8-959f3f526f91<br>**Similarity:** 0.92824387550354<br>**Text:** Allergy Suggested by:  being worse after contact with some 
substances, e.g. nylon underwear, chemicals, 
and soap.  
Confirmed by:  response to avoidance of precipitants.
Finalized by the predictable outcome of  management, 
e.g. emollient, with or without steroid creams or 
ointments.
Lichen sclerosis Suggested by:  being intensely itchy. Bruised, 
red, purpuric appearance. Bullae, erosions, and 
ulcerations. Later, white, flat, and shiny with an 
hourglass shape around the vulva and anus.
Confirmed by:  above clinical appearance and biopsy .
Finalized by the predictable outcome of  management, 
e.g. biopsy of any suspicious lesion. Topical steroids. 
Vulvectomy in advanced cases, if not responding to 
medical treatment. Follow-up to ensure resolution or 
to re-investigate.
Leukoplakia Suggested by:  itchiness and white vulval patches due to 
skin thickening and hypertrophy.
Confirmed by:  above clinical appearance and histology 
on biopsy .
Finalized by the predictable outcome of  management, 
e.g.<br>

**Node ID:** 9aee9f70-f865-4746-8620-8af0cd9a80a5<br>**Similarity:** 0.9281908273696899<br>**Text:** Allergic 
contact 
dermatitisSuggested by:  exposure to a potential allergen, e.g. hair dye.
Confirmed by:  improvement on removal of the offending agent.
Finalized by the predictable outcome of  management, e.g.  avoid 
causative agent. local steroid lotions.
Candidiasis 
e.g. due to 
diabetes 
mellitus, 
AIDS, or 
Cushing’s 
syndromeSuggested by:  itchy, symmetrical with ‘satellite’ pustules outside 
the outer edge of the skin rash. Symptoms and signs of 
underlying condition.
Confirmed by:  +ve swabs and skin scrapings for yeasts .
Finalized by the predictable outcome of  management, e.g.  local 
clotrimazole or miconazole for 2–4wk. Systemic treatment for 
non-responding cases.
Discoid 
eczemaSuggested by:  recurring itchy lesion in a middle-aged or an 
elderly man.
Confirmed by:  presence of coin-shaped lesions on the 
limbs with a symmetrical distribution. 
Finalized by the predictable outcome of  management, e.g.  potent 
steroid cream combined with an antibiotic.
Drug-induced 
eczemaSuggested by:  itchy skin with a history of recent drug ingestion.
Confirmed by:  improvement on withdrawal of offending agent.
Finalized by the predictable outcome of  management, e.g.<br>

**Node ID:** 6bb70100-5085-478f-9a4c-67f4af5d0759<br>**Similarity:** 0.9281271696090698<br>**Text:** removal 
of the cause; moisturizers, creams, and topical steroids. 
Antibiotics if there is infection.
Fungal 
infectionsSuggested by:  typical ring-like lesions (clearer centres) on the trunk 
and limbs in tinea corporis (ringworm) or lesions in the inner 
upper thigh, not involving the scrotum with an advancing scaly and 
pustular edge in tinea cruris.
Confirmed by:  microscopy and culture of skin scrapings. 
Wood’s UV light examination  for tinea capitis.
Finalized by the predictable outcome of  management, e.g.  local or 
systemic antifungal agents.
Seborrhoeic 
dermatitisSuggested by:  scalp and facial involvement, excessive dandruff with 
an itchy and scaly eruption, affecting sides of nose, scalp margin, 
eyebrows, and ear.
Confirmed by:  typical skin lesions and distribution. 
Finalized by the predictable outcome of  management, e.g.  medicated 
shampoo alone or following the application of 2% sulphur ± 
preceding 2% salicylic acid for scalp lesions. Facial lesions treated 
with combined antimicrobial and steroid creams.
Lichen 
simplex 
chronicusSuggested by:  history of repeated rubbing or scratching of an area 
as a habit or caused by stress; typically Asian or Chinese patient.
Confirmed by:  presence of a single plaque on the back of the neck 
or in the perineum.
Finalized by the predictable outcome of  management, e.g.  emollients 
and topical steroids.
Lichen 
planusSuggested by:  no FH, related to stress; presence of Koebner’s 
phenomenon.
Confirmed by:  itchy, well-defined, raised, shiny-surfaced lesions with 
a violaceous colour divided by white streaks ( wickman’s striae).
Finalized by the predictable outcome of  management, e.g.  topical 
steroids, systemic steroids for very extensive lesions.<br>

**Node ID:** 30b84fe9-4c28-482e-8de9-6e2c23815a31<br>**Similarity:** 0.9277516007423401<br>**Text:** »Clinical Findings
Itching is common but usually mild. The diagnosis is made 
by finding one or more classic lesions, such as oval, fawn-
colored plaques up to 2 cm in diameter. The centers of a few 
lesions may have a characteristic crinkled or “cigarette 
paper” appearance and a collarette scale, ie, a thin bit of scale 
that is bound at the periphery and free in the center. Lesions 
follow cleavage lines on the trunk (so-called Christmas tree 
pattern, Figure 6–24), and the proximal portions of the 
extremities are often involved. A variant that affects the 
flexures (axillae and groin), so-called inverse pityriasis 
rosea, and a papular variant, especially in patients with more 
darkly pigmented skin types, also occur. An initial lesion 
(“herald patch”) that is often larger than the later lesions 
often precedes the general eruption by 1–2 weeks. The erup -
tion usually lasts 6–8 weeks and heals without scarring.
 »Differential Diagnosis
Serologic testing for syphilis should be performed if clini -
cal risk factors are present. Palmar and plantar or mucous 
membrane lesions or adenopathy are features suggestive of 
secondary syphilis. Tinea corporis may present with a few 
red, slightly scaly plaques. Typically, the number of plaques 
of tinea corporis is significantly fewer than the number 
CMDT24_Ch06_p0102-p0169.indd   138 26/06/23   9:59 AMhttps://allebookstores.com<br>

**Node ID:** d6148870-a040-4331-8066-c8bfad3d1790<br>**Similarity:** 0.9277409315109253<br>**Text:** 286  •  The skin, hair and nails
Family and social history
Enquire about occupation and hobbies, as exposure to chemicals 
may cause contact dermatitis. If a rash consistently improves when a patient is away from work, the possibility of industrial dermatitis should be considered. Ask about alcohol consumption and confirm smoking status.
Document foreign travel and sun exposure if actinic damage, 
tropical infections or photosensitive eruptions are being considered. The risk of squamous cell and basal cell cancers increases with total lifetime sun exposure, and intense sun exposures leading to blistering burns are a risk factor for melanoma. The susceptibility of an individual to sun-induced damage can be determined by defining their skin type using the Fitzpatrick scale  
(Box 14.2).
Ask about a family history of atopy and skin conditions.The history of a skin disorder alone rarely enables a definite 
diagnosis, with perhaps the occasional exception: an itchy eruption that resembles a nettle rash, the individual components of which last less than 24 hours, is very likely to be urticaria; and an intensely itchy eruption that affects all body areas except the head (in adults) and is worse in bed at night should be considered to be scabies until proved otherwise.
The physical examination
Proper assessment of the skin involves all the human senses, with the exception of taste. Once we have listened to the patient’s history, we look at the rash or lesion, touch the skin, and occasionally use our sense of smell to diagnose infection and metabolic disorders such as trimethylaminuria (fish odour syndrome).
Examination of the skin should be performed under conditions 
of privacy in an adequately lit, warm room with, when appropriate, a chaperone present (p. 20).<br>

#RAG Evaluation Using TruLens

##SETUP

In [ ]:
from google.colab import drive
drive.mount("/content/drive/")

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [ ]:
WorkDir = "/content/drive/MyDrive/tensorflow_project/Disease Prediction/data/4.5 - Multilingual USE/"

In [ ]:
import os
os.chdir(WorkDir)

Install Library

In [ ]:
!pip install llama-index-postprocessor-cohere-rerank

In [ ]:
!pip install llama-index-vector-stores-mongodb
!pip install llama-index-embeddings-openai
!pip install llama-index
!pip install pymongo

Import Libray

In [ ]:
import time
import openai
import pymongo
import numpy as np
import pandas as pd

from tqdm import tqdm
from google.colab import userdata
from IPython.display import Markdown, display

from llama_index.core import Settings
from llama_index.llms.openai import OpenAI
from llama_index.core import StorageContext
from llama_index.core import VectorStoreIndex
from llama_index.core.query_engine import TransformQueryEngine
from llama_index.postprocessor.cohere_rerank import CohereRerank
from llama_index.vector_stores.mongodb import MongoDBAtlasVectorSearch
from llama_index.core.response.notebook_utils import display_source_node
from llama_index.core.indices.query.query_transform import HyDEQueryTransform

Loading Credentials

In [ ]:
openai.api_key = userdata.get('OPENAI_API_KEY')
os.environ['MONGO_URI'] = userdata.get('MONGO_URI')
os.environ['OPENAI_API_KEY'] = userdata.get('OPENAI_API_KEY')

Set up Global LLM

In [ ]:
Settings.llm = OpenAI(model="gpt-3.5-turbo-0125", temperature=0.1)

##MongoDB Atlas

In [ ]:
uri = userdata.get('MONGO_URI')

In [ ]:
# Create a new client and connect to the server
client = pymongo.MongoClient(uri)

# Send a ping to confirm a successful connection
try:
    client.admin.command('ping')
    print("Pinged your deployment. You successfully connected to MongoDB!")
except Exception as e:
    print(e)

Pinged your deployment. You successfully connected to MongoDB!


In [ ]:
store = MongoDBAtlasVectorSearch(mongodb_client = client,
                                 db_name = 'DeepSymp',
                                 collection_name = 'medical-textbook',
                                 index_name = 'vector_index')
storage_context = StorageContext.from_defaults(vector_store=store)

###Retrive From Database

In [ ]:
start = time.time()

index = VectorStoreIndex.from_vector_store(store)

end = time.time()

print(end - start)

1.5275814533233643


##Hypothetical Document Embeddings

In [ ]:
symptoms = "I am red rash around my male genital. I'm not gay and I didn't have sex yet"

In [ ]:
query_str = f"""If a patient presents with the following symptoms:\n
                {symptoms},\n
                please provide three possible diseases and reasons why using bullet points.\n
                Should the patient seek professional medical attention or opt for self-care at a pharmacy?\n
                Additionally, outline the treatment options for each identified diseases"""

Without HyDE

In [ ]:
cohere_api_key = userdata.get("COHERE_API_KEY")
cohere_rerank = CohereRerank(api_key=cohere_api_key, top_n=3)

In [ ]:
query_engine = index.as_query_engine(similarity_top_k=10,
                                     node_postprocessors=[cohere_rerank]
                                     )
response = query_engine.query(query_str)
display(Markdown(f"<b>{response}</b>"))

<b>- Dermatitis or folliculitis: These conditions can occur due to irritation from shaving the pubic hair, leading to a red rash.
- Intertrigo: Infected eczema in the skin creases can also cause a red rash in the genital area.
- Alopecia: Hair loss in the pubic region can sometimes be associated with skin conditions that cause a red rash.

The patient should seek professional medical attention to accurately diagnose the underlying cause of the red rash and receive appropriate treatment.

Treatment options may include:
- Dermatitis or folliculitis: Topical corticosteroids or antibiotics may be prescribed.
- Intertrigo: Antifungal or antibacterial creams may be recommended.
- Alopecia: Treatment may involve addressing the underlying cause and promoting hair regrowth.</b>

With HyDE

In [ ]:
hyde = HyDEQueryTransform(include_original=True)
hyde_query_engine = TransformQueryEngine(query_engine, hyde)
response = hyde_query_engine.query(query_str)
display(Markdown(f"<b>{response}</b>"))

<b>- Contact dermatitis: This can occur due to various irritants or allergens coming into contact with the skin, leading to a red rash. In this case, it could be triggered by personal hygiene products, fabrics, or other substances.
- Folliculitis: Inflammation of the hair follicles can result in redness and irritation in the genital area, especially if there is shaving involved.
- Intertrigo: This is a type of skin inflammation that occurs in skin creases, such as the groin area, due to friction, heat, and moisture, leading to a red rash.

The patient should seek professional medical attention to accurately diagnose the condition and receive appropriate treatment.

Treatment options may include:
- For contact dermatitis: Topical corticosteroids, antihistamines, and avoiding the triggering substance.
- For folliculitis: Warm compresses, antibacterial washes, and in severe cases, antibiotics.
- For intertrigo: Keeping the area dry, using antifungal creams, and wearing breathable clothing.</b>

In [ ]:
for n in response.source_nodes:
    display_source_node(n, source_length=2000)

**Node ID:** f953aeb7-8f0f-4b30-a558-23f5ecec1633<br>**Similarity:** 0.9360516<br>**Text:** Explain	what	you	are	going	to	do	and	why	it	is	necessary, 	
and	offer	a	chaperone. 	Record	the	chaperone’s 	name;	if	the	
offer is refused, record the fact. Apply alcohol gel and put on gloves. Allow the patient privacy to undress.
Ask the patient to stand and expose the area from his lower 
abdomen to the top of his thighs, unless you are examining the 
inguinoscrotal 	area.	In	this	case,	ask	him	to	lie	on	his	back	initially.
Skin
Examination sequence
• Look in turn at the groin, skin creases, perineum and 
scrotal skin for redness, swellings or ulcers. Note the hair 
distribution.
•	 If	you	see	any	swellings	in	the	groin,	palpate	these	and	
define	them	using	‘SPACESPIT’ 	(see	Box	3.8).
There may be alopecia or an infestation. Patients who shave 
their pubic hair may have dermatitis or folliculitis (infection around the base of the hairs), causing an irritating red rash. 
Intertrigo	(infected	eczema)	occurs	in	the	skin	creases,	and	
lymphadenopathy may stem from local or general causes.
Scrotal oedema can be caused by systemic or local disease. 
Heart	and	liver	dysfunction 	may	lead	to	significant	genital	oedema,	
as may nephrotic syndrome and lymphoedema due to pelvic lymphadenopathy.
Penis
Examination sequence
• Look at the shaft and check the position of the urethral 
opening to exclude hypospadias (urethra opening partway 
along the shaft of the penis; see Fig. 15.11A).
• Palpate the shaft for fibrous plaques (usually on the 
dorsum). Palpate any other lesions to define them.
• Retract the prepuce and inspect the glans for red patches 
or vesicles.Consider possible precipitating events: for example, relationship 
difficulties or trauma. Assess cardiovascular, neurological and psychiatric comorbidities as well as taking a drug history.
If	the	patient	has	never	had	an	erection,	he	may	have	primary	
ED	due	to	an	anatomical 	abnormality. 	Secondary 	ED	is	more	
common and may be psychological or organic in aetiology. 
Psychological 	ED	may	have	a	precipitating 	...<br>

**Node ID:** 9a7bbf98-c33d-40ac-81ae-bc9e1293935a<br>**Similarity:** 0.91413754<br>**Text:** Finalized by the predictable outcome of  management, e.g.  
paracetamol and antihistamines.
Chicken pox Suggested by:  contact with a case of chickenpox, a prodromal 
illness for –2d before the appearance of a rash.
Confirmed by:  erythematous lesions, rapidly changing to vesicles, then 
pustules, followed by crusts after 2–3d. lesions itchy.
Finalized by the predictable outcome of  management, e.g.  antipyretics, 
antihistamines, and calamine lotion to ease itching and irritability.
Herpes 
simplexSuggested by:  presence of contacts and occurring at a similar site 
each time, usually lips, face, or genitals, associated respiratory 
infection (‘cold sore’). lesions recurring.
Confirmed by:  presence of vesicles on the mouth or genitalia. 
Painful, later crusting with local lymphadenopathy.
Finalized by the predictable outcome of  management, e.g.  paracetamol 
for pain. Aciclovir cream applied five times daily for recurrent 
mild facial and genital infections. Aciclovir orally for more severe 
infections. Confirmed genital herpes in a pregnant woman at the time 
of delivery is an indication for Caesarean section.<br>

**Node ID:** 96c7889f-f31b-4c10-8442-24de6275c53f<br>**Similarity:** 0.8842394<br>**Text:** Common presenting symptoms
These include:
•	 a	rash:	scaly,	blistering	or	itchy
•	 a	lump	or	lesion•	 pruritus 	(itch)
•	 hair	loss	or	excess	hair	(hirsutism, 	hypertrichosis)
•	 nail	changes.
Ask:
•	 When	did	the	lesion	appear	or	the	rash	begin?
•	 Where 	is	the	rash/lesion?
•	 Has	the	rash	spread,	or	the	lesion	changed,	since	its	
onset?
•	 Is	the	lesion	tender	or	painful?	Is	the	rash	itchy?	Is	the	itch	
intense enough to cause bleeding by scratching or to 
disturb	sleep,	as	in	atopic	eczema	and	lichen	simplex?	Are	
there	blisters?
•	 Do	the	symptoms 	vary	with	time?	For	example,	the	
pruritus of scabies is usually worse at night, and acne  
and atopic eczema may show a premenstrual exacerbation.
•	 Were	there	any	preceding 	symptoms, 	such	as	a	 
sore throat in psoriasis, a severe illness in telogen effluvium, or a new oral medication in drug  
eruptions?
•	 Are	there	any	aggravating 	or	relieving	factors?	For	
example, exercise or exposure to heat may precipitate cholinergic urticaria.
•	 What,	if	any,	has	been	the	effect	of	topical	or	oral	
medications? 	Self-medication 	with	oral	antihistamines 	may	
ameliorate urticaria, and topical glucocorticoids may help inflammatory reactions.
•	 Are	there	any	associated 	constitutional 	symptoms, 	 
such as joint pain (psoriasis), muscle pain and  
weakness (dermatomyositis), fever, fatigue or  
weight	loss?
•	 Very	importantly, 	what	is	the	impact	of	the	rash	on	the	
individual’s 	quality	of	life?
Past medical and drug history
Ask about general health and previous medical or skin conditions; a history of asthma, hay fever or childhood eczema suggests atopy. Coeliac disease is associated with dermatitis herpetiformis.
Take a full drug history, including any recent oral or topical 
prescribed or over-the-counter medication. Enquire about allergies not just to medicines but also to animals or foods.
Fig. 14.2
 Structure of the nail.<br>

##TruLens

###SETUP

In [ ]:
!pip install trulens_eval

In [ ]:
from trulens_eval import Tru
tru = Tru()

/usr/local/lib/python3.10/dist-packages/_distutils_hack/__init__.py:33: UserWarning: Setuptools is replacing distutils.
  warnings.warn("Setuptools is replacing distutils.")


🦑 Tru initialized with db url sqlite:///default.sqlite .
🛑 Secret keys may be written to the database. See the `database_redact_keys` option of Tru` to prevent this.


In [ ]:
from trulens_eval.feedback.provider import OpenAI as OpenAI_trulens
from trulens_eval import Feedback

###Initialize Feedback Function(s)

In [ ]:
# Initialize provider class
provider = OpenAI_trulens()

# select context to be used in feedback. the location of context is app specific.
from trulens_eval.app import App
context = App.select_context(hyde_query_engine)

from trulens_eval.feedback import Groundedness
grounded = Groundedness(groundedness_provider=OpenAI_trulens())
# Define a groundedness feedback function
f_groundedness = (
    Feedback(grounded.groundedness_measure_with_cot_reasons)
    .on(context.collect()) # collect context chunks into a list
    .on_output()
    .aggregate(grounded.grounded_statements_aggregator)
)

# Question/answer relevance between overall question and answer.
f_answer_relevance = (
    Feedback(provider.relevance)
    .on_input_output()
)
# Question/statement relevance between question and each context chunk.
f_context_relevance = (
    Feedback(provider.context_relevance_with_cot_reasons)
    .on_input()
    .on(context)
    .aggregate(np.mean)
)

✅ In groundedness_measure_with_cot_reasons, input source will be set to __record__.app.query.rets.source_nodes[:].node.text.collect() .
✅ In groundedness_measure_with_cot_reasons, input statement will be set to __record__.main_output or `Select.RecordOutput` .
✅ In relevance, input prompt will be set to __record__.main_input or `Select.RecordInput` .
✅ In relevance, input response will be set to __record__.main_output or `Select.RecordOutput` .
✅ In context_relevance_with_cot_reasons, input question will be set to __record__.main_input or `Select.RecordInput` .
✅ In context_relevance_with_cot_reasons, input context will be set to __record__.app.query.rets.source_nodes[:].node.text .


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


###Instrument app for logging with TruLens

In [ ]:
from trulens_eval import TruLlama
tru_query_engine_recorder = TruLlama(hyde_query_engine,
    app_id='LlamaIndex_App1',
    feedbacks=[f_groundedness, f_answer_relevance, f_context_relevance])

In [ ]:
symptoms = " I have a known severe food allergy. I have been in contact with something that I am allergic to. I have a cramp and sharp pain in my flank (left side), iliac fossa (right side), and belly. The pain is intense, around a 6. The pain appeared quickly, an 8 out of 10. I feel lightheaded and dizzy, like I am about to faint. I have lesions on my skin that are pink in color, not peeling off, and swollen at a 4 out of 10 on my back of the neck, right bicep, left bicep, mouth, and right ankle. The pain caused by the rash is 0 out of 10 but the itching is very intense at 8 out of 10. I am feeling nauseous and have a swollen cheek on the right side and nose. I have noticed a high pitched sound when breathing in and wheezing when I exhale. I am more likely to develop common allergies than the general population."

query_str = f"""If a patient presents with the following symptoms:\n
                {symptoms},\n
                please provide three possible diseases and reasons why using bullet points.\n
                Should the patient seek professional medical attention or opt for self-care at a pharmacy?\n
                Additionally, outline the treatment options for each identified diseases"""

In [ ]:
# or as context manager
with tru_query_engine_recorder as recording:
    hyde_query_engine.query(query_str)

###Retrieve records and feedback

In [ ]:
# The record of the app invocation can be retrieved from the `recording`:

rec = recording.get() # use .get if only one record
# recs = recording.records # use .records if multiple

display(rec)

Record(record_id='record_hash_8b938b57510fb0685bb6a80e20c250eb', app_id='LlamaIndex_App1', cost=Cost(n_requests=4, n_successful_requests=4, n_classes=0, n_tokens=3505, n_stream_chunks=0, n_prompt_tokens=2967, n_completion_tokens=538, cost=0.0020065), perf=Perf(start_time=datetime.datetime(2024, 4, 12, 10, 32, 2, 965641), end_time=datetime.datetime(2024, 4, 12, 10, 32, 15, 497790)), ts=datetime.datetime(2024, 4, 12, 10, 32, 15, 500738), tags='-', meta=None, main_input='If a patient presents with the following symptoms:\n\n                 I have a known severe food allergy. I have been in contact with something that I am allergic to. I have a cramp and sharp pain in my flank (left side), iliac fossa (right side), and belly. The pain is intense, around a 6. The pain appeared quickly, an 8 out of 10. I feel lightheaded and dizzy, like I am about to faint. I have lesions on my skin that are pink in color, not peeling off, and swollen at a 4 out of 10 on my back of the neck, right bicep, le

In [ ]:
tru.run_dashboard()

Starting dashboard ...
Config file already exists. Skipping writing process.
Credentials file already exists. Skipping writing process.
Dashboard already running at path:   Submit this IP Address: 34.23.1.121



<Popen: returncode: None args: ['streamlit', 'run', '--server.headless=True'...>

In [ ]:
# The results of the feedback functions can be rertireved from
# `Record.feedback_results` or using the `wait_for_feedback_result` method. The
# results if retrieved directly are `Future` instances (see
# `concurrent.futures`). You can use `as_completed` to wait until they have
# finished evaluating or use the utility method:

for feedback, feedback_result in rec.wait_for_feedback_results().items():
    print(feedback.name, feedback_result.result)

# See more about wait_for_feedback_results:
# help(rec.wait_for_feedback_results)

groundedness_measure_with_cot_reasons 0.5
relevance 0.9
context_relevance_with_cot_reasons 0.9333333333333332


In [ ]:
records, feedback = tru.get_records_and_feedback(app_ids=["LlamaIndex_App1"])

records.head()

app_id                                           app_json  \
0  LlamaIndex_App1  {"tru_class_info": {"name": "TruLlama", "modul...   
1  LlamaIndex_App1  {"tru_class_info": {"name": "TruLlama", "modul...   
2  LlamaIndex_App1  {"tru_class_info": {"name": "TruLlama", "modul...   
3  LlamaIndex_App1  {"tru_class_info": {"name": "TruLlama", "modul...   

                                                type  \
0  TransformQueryEngine(llama_index.core.query_en...   
1  TransformQueryEngine(llama_index.core.query_en...   
2  TransformQueryEngine(llama_index.core.query_en...   
3  TransformQueryEngine(llama_index.core.query_en...   

                                      record_id  \
0  record_hash_829c7f9c521747e9c6db87c7f0ef954e   
1  record_hash_b4da49be70753a6d3be2d5d18279bd0b   
2  record_hash_00aa16b127ff67aa5d12d0b03659c9a4   
3  record_hash_8b938b57510fb0685bb6a80e20c250eb   

                                               input  \
0               "What did the author do growing up?"   
1  "If a patient presents with the following symp...   
2  "If a patient presents with the following symp...   
3  "If a patient presents with the following symp...   

                                              output tags  \
0  "The author learned to walk and run ahead of h...    -   
1  "- Contact dermatitis: The red rash could be d...    -   
2  "- Contact dermatitis: This condition can occu...    -   
3  "- Anaphylaxis:\n  - Known severe food allergy...    -   

                                         record_json  \
0  {"record_id": "record_hash_829c7f9c521747e9c6d...   
1  {"record_id": "record_hash_b4da49be70753a6d3be...   
2  {"record_id": "record_hash_00aa16b127ff67aa5d1...   
3  {"record_id": "record_hash_8b938b57510fb0685bb...   

                                           cost_json  \
0  {"n_requests": 2, "n_successful_requests": 2, ...   
1  {"n_requests": 2, "n_successful_requests": 2, ...   
2  {"n_requests": 4, "n_successful_requests": 4, ...   
3  {"n_requests": 4, "n_successful_requests": 4, ...   

                                           perf_json  \
0  {"start_time": "2024-04-12T09:55:07.481206", "...   
1  {"start_time": "2024-04-12T09:55:46.432491", "...   
2  {"start_time": "2024-04-12T10:01:24.386659", "...   
3  {"start_time": "2024-04-12T10:32:02.965641", "...   

                           ts  relevance  \
0  2024-04-12T09:55:11.778883        0.2   
1  2024-04-12T09:55:53.670128        0.8   
2  2024-04-12T10:01:35.800558        0.9   
3  2024-04-12T10:32:15.500738        0.9   

   groundedness_measure_with_cot_reasons  context_relevance_with_cot_reasons  \
0                                    0.0                            0.240000   
1                                    0.0                            0.790000   
2                                    0.0                            0.810000   
3                                    0.5                            0.933333   

                                     relevance_calls  \
0  [{'args': {'prompt': 'What did the author do g...   
1  [{'args': {'prompt': 'If a patient presents wi...   
2  [{'args': {'prompt': 'If a patient presents wi...   
3  [{'args': {'prompt': 'If a patient presents wi...   

         groundedness_measure_with_cot_reasons_calls  \
0  [{'args': {'source': ['The fertile earth, the ...   
1  [{'args': {'source': ['Explain\twhat\tyou\tare...   
2  [{'args': {'source': ['Explain\twhat\tyou\tare...   
3  [{'args': {'source': ['CHAPTER  22\n 874\n CMD...   

            context_relevance_with_cot_reasons_calls  latency  total_tokens  \
0  [{'args': {'question': 'What did the author do...        4          2525   
1  [{'args': {'question': 'If a patient presents ...        7          6217   
2  [{'args': {'question': 'If a patient presents ...       11          5982   
3  [{'args': {'question': 'If a patient presents ...       12          3505   

   total_cost  
0    0.001270  
1    0.003274  
2    0.003299  
3    0.002007

In [ ]:
tru.get_leaderboard(app_ids=["LlamaIndex_App1"])

context_relevance_with_cot_reasons  relevance  \
app_id                                                           
LlamaIndex_App1                            0.693333        0.7   

                 groundedness_measure_with_cot_reasons  latency  total_cost  
app_id                                                                       
LlamaIndex_App1                                  0.125      8.5    0.002462

###Explore in a Dashboard

In [ ]:
tru.run_dashboard() # open a local streamlit app to explore

# tru.stop_dashboard() # stop if needed

Starting dashboard ...
Config file already exists. Skipping writing process.
Credentials file already exists. Skipping writing process.
Dashboard already running at path:   Submit this IP Address: 34.23.1.121



<Popen: returncode: None args: ['streamlit', 'run', '--server.headless=True'...>

#RAG In Production

##SETUP

In [ ]:
from google.colab import drive
drive.mount("/content/drive/")

Mounted at /content/drive/


In [ ]:
WorkDir = "/content/drive/MyDrive/tensorflow_project/Disease Prediction/data/4.5 - Multilingual USE/"

In [ ]:
import os
os.chdir(WorkDir)

Install Library

In [ ]:
!pip install llama-index-postprocessor-cohere-rerank

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 150.6/150.6 kB 3.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 11.5 MB/s eta 0:00:00


In [ ]:
!pip install llama-index-vector-stores-mongodb
!pip install llama-index-embeddings-openai
!pip install llama-index
!pip install pymongo

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.4/15.4 MB 29.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 676.9/676.9 kB 43.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 7.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.8/132.8 kB 12.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.3/268.3 kB 23.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 44.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 307.7/307.7 kB 25.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 7.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 6.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 5.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 26.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.9/3.9 MB 66.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━

Import Libray

In [ ]:
import time
import openai
import pymongo
import numpy as np
import pandas as pd

from tqdm import tqdm
from google.colab import userdata
from IPython.display import Markdown, display

from llama_index.core import Settings
from llama_index.llms.openai import OpenAI
from llama_index.core import StorageContext
from llama_index.core import VectorStoreIndex
from llama_index.core.query_engine import TransformQueryEngine
from llama_index.vector_stores.mongodb import MongoDBAtlasVectorSearch
from llama_index.core.response.notebook_utils import display_source_node
from llama_index.core.indices.query.query_transform import HyDEQueryTransform

Loading Credentials

In [ ]:
openai.api_key = userdata.get('OPENAI_API_KEY')
os.environ['MONGO_URI'] = userdata.get('MONGO_URI')
os.environ['OPENAI_API_KEY'] = userdata.get('OPENAI_API_KEY')

Set up Global LLM

In [ ]:
Settings.llm = OpenAI(model="gpt-3.5-turbo-0125", temperature=0.1)

##MongoDB Atlas

In [ ]:
uri = userdata.get('MONGO_URI')

In [ ]:
# Create a new client and connect to the server
client = pymongo.MongoClient(uri)

# Send a ping to confirm a successful connection
try:
    client.admin.command('ping')
    print("Pinged your deployment. You successfully connected to MongoDB!")
except Exception as e:
    print(e)

Pinged your deployment. You successfully connected to MongoDB!


In [ ]:
store = MongoDBAtlasVectorSearch(mongodb_client = client,
                                 db_name = 'DeepSymp',
                                 collection_name = 'medical-textbook',
                                 index_name = 'vector_index')
storage_context = StorageContext.from_defaults(vector_store=store)

###Retrive From Database

In [ ]:
start = time.time()

index = VectorStoreIndex.from_vector_store(store)

end = time.time()

print(end - start)

0.543196439743042


##Hypothetical Document Embeddings

In [ ]:
symptoms = " I am red rash around my male genital. I'm not gay and I didn't have sex yet"

In [ ]:
query_str = f"""If a patient presents with the following symptoms:\n
                {symptoms},\n
                please provide three possible diseases and reasons why using bullet points.\n
                Should the patient seek professional medical attention or opt for self-care at a pharmacy?\n
                Additionally, outline the treatment options for each identified diseases"""

Without HyDE

In [ ]:
cohere_api_key = userdata.get("COHERE_API_KEY")
cohere_rerank = CohereRerank(api_key=cohere_api_key, top_n=3)

In [ ]:
query_engine = index.as_query_engine(similarity_top_k=10,
                                     node_postprocessors=[cohere_rerank]
                                     )
response = query_engine.query(query_str)
display(Markdown(f"<b>{response}</b>"))

<b>- Contact Dermatitis: Red rash around the male genital area can be caused by contact dermatitis, which is a skin reaction to irritants or allergens coming into contact with the skin.
- Folliculitis: Infection around the base of the hairs can lead to redness and rash in the genital area, especially if there is shaving involved.
- Intertrigo: Infected eczema that occurs in skin creases can also present as a red rash in the genital area.

The patient should seek professional medical attention to accurately diagnose the underlying cause of the rash and receive appropriate treatment.

Treatment options:
- Contact Dermatitis: Topical corticosteroids, antihistamines, and avoiding the irritant or allergen.
- Folliculitis: Antibacterial or antifungal creams, warm compresses, and proper hygiene.
- Intertrigo: Topical antifungal or steroid creams, keeping the area dry and clean, and wearing loose-fitting clothing.</b>

With HyDE

In [ ]:
hyde = HyDEQueryTransform(include_original=True)
hyde_query_engine = TransformQueryEngine(query_engine, hyde)
response = hyde_query_engine.query(query_str)
display(Markdown(f"<b>{response}</b>"))

<b>- Contact dermatitis: Exposure to potential allergens like certain fabrics or personal care products can cause a red rash. It may improve upon avoiding the causative agent.
- Candidiasis: Itchy rash with 'satellite' pustules outside the rash's edge can be a sign of candidiasis, especially in individuals with conditions like diabetes. Treatment includes local clotrimazole or miconazole.
- Herpes simplex virus type 2: Genital herpes can present with multiple vesicles on the genitals leading to painful ulcerations. It is important to seek professional medical attention for proper diagnosis and management.

For these conditions, seeking professional medical attention is recommended for accurate diagnosis and appropriate treatment. Treatment options may include:
- Contact dermatitis: Avoiding the allergen, using emollients, and local steroid lotions.
- Candidiasis: Local clotrimazole or miconazole for mild cases, systemic treatment for non-responding cases.
- Herpes simplex virus type 2: Antiviral medications like aciclovir for recurrent infections, and in severe cases, oral antiviral therapy may be necessary.</b>

In [ ]:
for n in response.source_nodes:
    display_source_node(n, source_length=2000)

**Node ID:** 96c7889f-f31b-4c10-8442-24de6275c53f<br>**Similarity:** 0.9319285154342651<br>**Text:** Common presenting symptoms
These include:
•	 a	rash:	scaly,	blistering	or	itchy
•	 a	lump	or	lesion•	 pruritus 	(itch)
•	 hair	loss	or	excess	hair	(hirsutism, 	hypertrichosis)
•	 nail	changes.
Ask:
•	 When	did	the	lesion	appear	or	the	rash	begin?
•	 Where 	is	the	rash/lesion?
•	 Has	the	rash	spread,	or	the	lesion	changed,	since	its	
onset?
•	 Is	the	lesion	tender	or	painful?	Is	the	rash	itchy?	Is	the	itch	
intense enough to cause bleeding by scratching or to 
disturb	sleep,	as	in	atopic	eczema	and	lichen	simplex?	Are	
there	blisters?
•	 Do	the	symptoms 	vary	with	time?	For	example,	the	
pruritus of scabies is usually worse at night, and acne  
and atopic eczema may show a premenstrual exacerbation.
•	 Were	there	any	preceding 	symptoms, 	such	as	a	 
sore throat in psoriasis, a severe illness in telogen effluvium, or a new oral medication in drug  
eruptions?
•	 Are	there	any	aggravating 	or	relieving	factors?	For	
example, exercise or exposure to heat may precipitate cholinergic urticaria.
•	 What,	if	any,	has	been	the	effect	of	topical	or	oral	
medications? 	Self-medication 	with	oral	antihistamines 	may	
ameliorate urticaria, and topical glucocorticoids may help inflammatory reactions.
•	 Are	there	any	associated 	constitutional 	symptoms, 	 
such as joint pain (psoriasis), muscle pain and  
weakness (dermatomyositis), fever, fatigue or  
weight	loss?
•	 Very	importantly, 	what	is	the	impact	of	the	rash	on	the	
individual’s 	quality	of	life?
Past medical and drug history
Ask about general health and previous medical or skin conditions; a history of asthma, hay fever or childhood eczema suggests atopy. Coeliac disease is associated with dermatitis herpetiformis.
Take a full drug history, including any recent oral or topical 
prescribed or over-the-counter medication. Enquire about allergies not just to medicines but also to animals or foods.
Fig. 14.2
 Structure of the nail.<br>

**Node ID:** f953aeb7-8f0f-4b30-a558-23f5ecec1633<br>**Similarity:** 0.9310309886932373<br>**Text:** Explain	what	you	are	going	to	do	and	why	it	is	necessary, 	
and	offer	a	chaperone. 	Record	the	chaperone’s 	name;	if	the	
offer is refused, record the fact. Apply alcohol gel and put on gloves. Allow the patient privacy to undress.
Ask the patient to stand and expose the area from his lower 
abdomen to the top of his thighs, unless you are examining the 
inguinoscrotal 	area.	In	this	case,	ask	him	to	lie	on	his	back	initially.
Skin
Examination sequence
• Look in turn at the groin, skin creases, perineum and 
scrotal skin for redness, swellings or ulcers. Note the hair 
distribution.
•	 If	you	see	any	swellings	in	the	groin,	palpate	these	and	
define	them	using	‘SPACESPIT’ 	(see	Box	3.8).
There may be alopecia or an infestation. Patients who shave 
their pubic hair may have dermatitis or folliculitis (infection around the base of the hairs), causing an irritating red rash. 
Intertrigo	(infected	eczema)	occurs	in	the	skin	creases,	and	
lymphadenopathy may stem from local or general causes.
Scrotal oedema can be caused by systemic or local disease. 
Heart	and	liver	dysfunction 	may	lead	to	significant	genital	oedema,	
as may nephrotic syndrome and lymphoedema due to pelvic lymphadenopathy.
Penis
Examination sequence
• Look at the shaft and check the position of the urethral 
opening to exclude hypospadias (urethra opening partway 
along the shaft of the penis; see Fig. 15.11A).
• Palpate the shaft for fibrous plaques (usually on the 
dorsum). Palpate any other lesions to define them.
• Retract the prepuce and inspect the glans for red patches 
or vesicles.Consider possible precipitating events: for example, relationship 
difficulties or trauma. Assess cardiovascular, neurological and psychiatric comorbidities as well as taking a drug history.
If	the	patient	has	never	had	an	erection,	he	may	have	primary	
ED	due	to	an	anatomical 	abnormality. 	Secondary 	ED	is	more	
common and may be psychological or organic in aetiology. 
Psychological 	ED	may	have	a	precipitating 	...<br>

**Node ID:** c8350183-09c6-4cbb-8fbc-930b6e032664<br>**Similarity:** 0.9296298027038574<br>**Text:** emollient, antihistamines, 
withdrawal of most recently used drugs, e.g. 
antibiotics.
Viral exanthema from 
unknown agentSuggested by:  red, non-itchy rash with uniform 
pigmentation. Related systemic symptoms.
Confirmed by:  appearance, spontaneous 
resolution.
Finalized by the predictable outcome of  
management, e.g.  antipyretic.
Measles Suggested by:  red, non-itchy rash with uniform 
pigmentation. Related systemic symptoms.
Confirmed by:  appearance, spontaneous 
resolution, consistent with an incubation 
period of 0–4 days. 
Finalized by the predictable outcome of  
management, e.g.  antipyretic.
Rubella (in pregnant 
mothers complicated by 
congential malformation)Suggested by:  red, non-itchy rash with uniform 
pigmentation. Related systemic symptoms.
Confirmed by:  appearance, spontaneous 
resolution, consistent with an incubation 
period of 4–2 days.<br>

**Node ID:** bc7078a9-e5b6-4009-9e8e-deac952d331f<br>**Similarity:** 0.9278008937835693<br>**Text:** Page 312 / 394In men: balanitis/balanoposthitis
(inﬂammation of the glans/prepuce,
erythema, pruritus, white pustules)
and rarely urethritispH of vaginal ﬂuid:
normalIn men:
miconazole 2%
cream: 1 application
2 times daily for 7
days
Herpes
simplex
virus type 2
(genital herpes)Many asymptomatic carriers. Multiple
vesicles on genitals leading to painful
ulcerations. In women, affects vulva,
vagina and cervix; in males, penis and
sometimes urethra.<br>

**Node ID:** 9aee9f70-f865-4746-8620-8af0cd9a80a5<br>**Similarity:** 0.9269028902053833<br>**Text:** Allergic 
contact 
dermatitisSuggested by:  exposure to a potential allergen, e.g. hair dye.
Confirmed by:  improvement on removal of the offending agent.
Finalized by the predictable outcome of  management, e.g.  avoid 
causative agent. local steroid lotions.
Candidiasis 
e.g. due to 
diabetes 
mellitus, 
AIDS, or 
Cushing’s 
syndromeSuggested by:  itchy, symmetrical with ‘satellite’ pustules outside 
the outer edge of the skin rash. Symptoms and signs of 
underlying condition.
Confirmed by:  +ve swabs and skin scrapings for yeasts .
Finalized by the predictable outcome of  management, e.g.  local 
clotrimazole or miconazole for 2–4wk. Systemic treatment for 
non-responding cases.
Discoid 
eczemaSuggested by:  recurring itchy lesion in a middle-aged or an 
elderly man.
Confirmed by:  presence of coin-shaped lesions on the 
limbs with a symmetrical distribution. 
Finalized by the predictable outcome of  management, e.g.  potent 
steroid cream combined with an antibiotic.
Drug-induced 
eczemaSuggested by:  itchy skin with a history of recent drug ingestion.
Confirmed by:  improvement on withdrawal of offending agent.
Finalized by the predictable outcome of  management, e.g.<br>

**Node ID:** 923bb485-9445-44b8-b2f8-959f3f526f91<br>**Similarity:** 0.9267577528953552<br>**Text:** Allergy Suggested by:  being worse after contact with some 
substances, e.g. nylon underwear, chemicals, 
and soap.  
Confirmed by:  response to avoidance of precipitants.
Finalized by the predictable outcome of  management, 
e.g. emollient, with or without steroid creams or 
ointments.
Lichen sclerosis Suggested by:  being intensely itchy. Bruised, 
red, purpuric appearance. Bullae, erosions, and 
ulcerations. Later, white, flat, and shiny with an 
hourglass shape around the vulva and anus.
Confirmed by:  above clinical appearance and biopsy .
Finalized by the predictable outcome of  management, 
e.g. biopsy of any suspicious lesion. Topical steroids. 
Vulvectomy in advanced cases, if not responding to 
medical treatment. Follow-up to ensure resolution or 
to re-investigate.
Leukoplakia Suggested by:  itchiness and white vulval patches due to 
skin thickening and hypertrophy.
Confirmed by:  above clinical appearance and histology 
on biopsy .
Finalized by the predictable outcome of  management, 
e.g.<br>

**Node ID:** 677961b0-1d8d-4e8d-b84b-61cf5b7e6294<br>**Similarity:** 0.9267153739929199<br>**Text:** Pruritus accompanying serious internal disease may not 
respond to any type of therapy.
Jeon J et al. Treatment of patients with chronic pruritus of 
unknown origin with dupilumab. J Dermatolog Treat. 2022;  
33:1754. [PMID: 33557654]
Kabashima K et al; Nemolizumab-JP01 Study Group. Trial of 
nemolizumab and topical agents for atopic dermatitis with 
pruritus. N Engl J Med. 2020;383:141. [PMID: 32640132]
Misery L et al. Chronic itch: emerging treatments following new 
research concepts. Br J Pharmacol. 2021;178:4775. [PMID: 
34463358]
Satoh T et al. 2020 guidelines for the diagnosis and treatment 
of cutaneous pruritus. J Dermatol. 2021;48:e399. [PMID: 
34288036]
Sutaria N et al. Itch: pathogenesis and treatment. J Am Acad 
Dermatol. 2022;86:17. [PMID: 34648873]
Anogenital Pruritus
ESSENTIALS OF DIAGNOSIS
 »Anogenital itching, chiefly nocturnal.
 »Skin findings are highly variable, ranging from 
none to excoriations and inflammation of any 
degree, including lichenification.
 »General Considerations
Anogenital pruritus may be due to a primary inflammatory 
skin disease (intertrigo, psoriasis, lichen simplex chronicus, 
seborrheic dermatitis, lichen sclerosus), contact dermatitis 
(soaps, wipes, colognes, douches, and topical treatments), 
irritating secretions (diarrhea, leukorrhea, or trichomonia -
sis), infections (candidiasis, dermatophytosis, erythrasma), 
or oxyuriasis (pinworms). Erythrasma is diagnosed by coral-
red fluorescence with Wood light and cured with erythromy -
cin. Squamous cell carcinoma of the anus and extramammary 
Paget disease are rare causes of genital pruritus.
In pruritus ani, hemorrhoids are often found, and leak -
age of mucus and bacteria from the distal rectum onto the 
perianal skin may be important in cases in which no other 
skin abnormality is found.
Many women experience pruritus vulvae. Pruritus vul -
vae does not usually involve the anal area, though anal itch -
ing may spread to the vulva. In men, pruritus of the scrotum 
is ...<br>

**Node ID:** 9a7bbf98-c33d-40ac-81ae-bc9e1293935a<br>**Similarity:** 0.9266722202301025<br>**Text:** Finalized by the predictable outcome of  management, e.g.  
paracetamol and antihistamines.
Chicken pox Suggested by:  contact with a case of chickenpox, a prodromal 
illness for –2d before the appearance of a rash.
Confirmed by:  erythematous lesions, rapidly changing to vesicles, then 
pustules, followed by crusts after 2–3d. lesions itchy.
Finalized by the predictable outcome of  management, e.g.  antipyretics, 
antihistamines, and calamine lotion to ease itching and irritability.
Herpes 
simplexSuggested by:  presence of contacts and occurring at a similar site 
each time, usually lips, face, or genitals, associated respiratory 
infection (‘cold sore’). lesions recurring.
Confirmed by:  presence of vesicles on the mouth or genitalia. 
Painful, later crusting with local lymphadenopathy.
Finalized by the predictable outcome of  management, e.g.  paracetamol 
for pain. Aciclovir cream applied five times daily for recurrent 
mild facial and genital infections. Aciclovir orally for more severe 
infections. Confirmed genital herpes in a pregnant woman at the time 
of delivery is an indication for Caesarean section.<br>

**Node ID:** d6148870-a040-4331-8066-c8bfad3d1790<br>**Similarity:** 0.926637589931488<br>**Text:** 286  •  The skin, hair and nails
Family and social history
Enquire about occupation and hobbies, as exposure to chemicals 
may cause contact dermatitis. If a rash consistently improves when a patient is away from work, the possibility of industrial dermatitis should be considered. Ask about alcohol consumption and confirm smoking status.
Document foreign travel and sun exposure if actinic damage, 
tropical infections or photosensitive eruptions are being considered. The risk of squamous cell and basal cell cancers increases with total lifetime sun exposure, and intense sun exposures leading to blistering burns are a risk factor for melanoma. The susceptibility of an individual to sun-induced damage can be determined by defining their skin type using the Fitzpatrick scale  
(Box 14.2).
Ask about a family history of atopy and skin conditions.The history of a skin disorder alone rarely enables a definite 
diagnosis, with perhaps the occasional exception: an itchy eruption that resembles a nettle rash, the individual components of which last less than 24 hours, is very likely to be urticaria; and an intensely itchy eruption that affects all body areas except the head (in adults) and is worse in bed at night should be considered to be scabies until proved otherwise.
The physical examination
Proper assessment of the skin involves all the human senses, with the exception of taste. Once we have listened to the patient’s history, we look at the rash or lesion, touch the skin, and occasionally use our sense of smell to diagnose infection and metabolic disorders such as trimethylaminuria (fish odour syndrome).
Examination of the skin should be performed under conditions 
of privacy in an adequately lit, warm room with, when appropriate, a chaperone present (p. 20).<br>

**Node ID:** 6ec0e3ce-75a6-4910-ba3c-5e65108e1b73<br>**Similarity:** 0.9255883693695068<br>**Text:** [PMID: 34456130]
3. Fungal rashes—
a. Rashes due to dermatophytes and candida —
Most fungal rashes afflicting patients with AIDS are due to 
dermatophytes and Candida.  While particularly common 
in the inguinal region, they may occur anywhere on the 
body. Fungal rashes generally respond well to topical 
clotrimazole (1% cream twice a day) or ketoconazole (2% 
cream twice a day).
b. Eosinophilic folliculitis —Eosinophilic folliculitis 
is a pruritic skin eruption with eosinophilic infiltration of 
hair follicles leading to papules or pustules, predominantly 
located on the scalp, face, neck, and torso. Eosinophilic fol -
liculitis in advanced HIV is thought to be noninfectious 
although the pathophysiology is unknown. The mainstay 
of treatment is topical corticosteroids with ART and 
isotretinoin therapy in severe cases.
c. Seborrheic dermatitis —This is more common in 
people with HIV . Scrapings of seborrhea have revealed 
Malassezia furfur  (Pityrosporum ovale ), implying that the 
seborrhea is caused by this fungus. A consistent finding is 
that seborrhea responds well to topical clotrimazole (1% 
cream) as well as hydrocortisone (1% cream).
4. Neoplastic dermatitides— See Chapter 6 and the Kaposi 
sarcoma section below.
5. Nonspecific dermatitides—
a. Xerosis —This condition presents in people with HIV 
with severe pruritus. The patient may have no rash, or 
nonspecific excoriations from scratching. Treatment is 
with emollients (eg, absorption base cream) and antipru -
ritic lotions (eg, camphor 9.5% and menthol 0.5%).
b. Psoriasis —Psoriasis can be very severe in people with 
HIV . Phototherapy, topical retinoids, and etretinate (0.25–
9.75 mg/kg/day orally in divided doses) may be used for 
recalcitrant cases in consultation with a dermatologist.L. HIV-Related Malignancies
Four cancers are included in the CDC classification of 
AIDS: Kaposi sarcoma, non-Hodgkin lymphoma, primary 
lymphoma of the brain, and invasive cervical carcinoma. 
Epidemiologic stu...<br>